## Лабораторная работа 5. Базовое использование Stable Diffusion

Здесь мы продолжаем работу с генеративными моделями для изображений. В прошлой части этой лабораторной работы мы создали синтетический датасет для классификации изображений. Теперь мы попробуем обучить классификатор на этих данных и проверить, насколько хорошо он будет различать реальных кошек и собак. Первым делом загрузим сохраненный датасет с диска. Кроме того загрузим так ` test dataset`, в качестве которого у нас будет выступать датасет реальных изображений кошек и собак. На нем мы будем проверять нашу идею, что в качестве тренировочных данных для обучения классификатора можно использовать синтетический датасет.

In [ ]:
from datasets import Dataset


train_dataset = Dataset.load_from_disk("./classification-dataset")

test_dataset = Dataset.load_from_disk("./classification-dataset-test")

В качестве модели для классификации выберем Vision Transformer (ViT). Так же определим несколько служебных функций.

In [ ]:
import torch
from transformers import ViTForImageClassification, ViTImageProcessor


labels = ["cat", "dog"]
model_name_or_path = 'google/vit-base-patch16-224-in21k'

processor = ViTImageProcessor.from_pretrained(model_name_or_path)

def transform(example_batch):
    inputs = processor([x for x in example_batch['image']], return_tensors='pt')
    inputs['labels'] = example_batch['labels']
    return inputs

def collate_fn(batch):
    return {
        'pixel_values': torch.stack([x['pixel_values'] for x in batch]),
        'labels': torch.tensor([x['labels'] for x in batch])
    }

model = ViTForImageClassification.from_pretrained(
    model_name_or_path,
    num_labels=len(labels),
    id2label={str(i): c for i, c in enumerate(labels)},
    label2id={c: str(i) for i, c in enumerate(labels)}
)

ds_train = train_dataset.with_transform(transform)
ds_test = test_dataset.with_transform(transform)

Определим метрику, которой мы будем пользоваться. В данном случае удобной будет метрика точность (`accuracy`). Объясните почему? В каких случаях использование этой метрики было бы неоправданным?

In [ ]:
import numpy as np
import evaluate

metric = evaluate.load("accuracy")
def compute_metrics(p):
    return metric.compute(predictions=np.argmax(p.predictions, axis=1), references=p.label_ids)

Ответ. Мы используем метрику точность потому, что ...

Теперь определим аргументы для обучения модели. Подберите оптимальный `batch_size` и `num_train_epochs`.

In [ ]:
from transformers import TrainingArguments

training_args = TrainingArguments(
    output_dir="./vit-base-cat-dogs",
    per_device_train_batch_size=16,
    eval_strategy="steps",
    eval_steps=4,
    save_strategy="steps",
    num_train_epochs=3,
    fp16=True,
    learning_rate=2e-4,
    save_total_limit=2,
    remove_unused_columns=False,
    push_to_hub=False,
    load_best_model_at_end=True,
)

Определите `Trainer`-объект с описанными выше параметрами. В качестве `data_collator` используйте `collate_fn`, а в качестве `tokenizer` используйте `processor`.

Запустите обучение

In [ ]:
train_results = trainer.train()

Выведите график `accuracy` и `validation loss` с помощью функции `matplotlib.pyplot.plot()`. Найдите точку ранней остановки, определите момент переобучения. Попробуйте расширить синтетический датасет. Принесет ли это пользу?